Лабораторная работа #3. Реализовать применение нескольких типов индексов для получения ранжированной выдачи источников из лабораторной работы #1 по поисковому запросу, сформулированному на естественном языке.

In [107]:
import re
from collections import defaultdict
from sklearn.feature_extraction.text import TfidfVectorizer

# Чтение текста страниц из файла content.txt
def read_content_file(filepath):
    with open(filepath, 'r', encoding='utf-8') as file:
        content = file.read().strip()
    pages = content.split('---page---')
    return [page.strip() for page in pages if page.strip()]

# Чтение мета данных из файла meta_info.txt
def read_meta_file(filepath):
    with open(filepath, 'r', encoding='utf-8') as file:
        meta = file.read()
    return meta

path = r'/Users/vlad-zharkov/Documents/Учеба/inf_search/‹ ¡  1/scraped_data_3/www_sports_ru/content_3.txt'
path_processed = r'/Users/vlad-zharkov/Documents/Учеба/inf_search/‹ ¡  2/processed_content_3.txt'
content_pages = read_content_file(path_processed)

meta = read_meta_file(r"/Users/vlad-zharkov/Documents/Учеба/inf_search/‹ ¡  1/scraped_data_3/meta_info_www_sports_ru_3.txt")

# Парсинг мета данных
def parse_meta(meta):
    meta_data = []
    url_pattern = re.compile(r'URL: (.+)')
    text_length_pattern = re.compile(r'Text Length: (\d+)')
    meta_lines = meta.strip().split('\n')
    
    current_url = None
    for line in meta_lines:
        url_match = url_pattern.match(line)
        text_length_match = text_length_pattern.match(line)
        
        if url_match:
            current_url = url_match.group(1)
        elif text_length_match:
            text_length = int(text_length_match.group(1))
            meta_data.append({
                "url": current_url,
                "text_length": text_length
            })
    
    return meta_data

meta_data = parse_meta(meta)

data = []
for idx, doc in enumerate(meta_data):
    print(content_pages[idx])
    data.append({
        "id": idx + 1,
        "url": doc["url"],
        "content": content_pages[idx]
    })



карло анчелотти высоко отозвался винисиусе футбол главная главная группа реал боруссия махачев порье трибуна ставки спорт казахстана футбол фигурка хоккей баскет теннис бокс авто лыжи наши приложения ставки главная группа новости трибуна букмекеры бонусы букмекеров приложения букмекеров зарубежные букмекеры букмекеры кэшбеком ставки киберспорт легальные букмекеры спорт казахстана главная группа новости трибуна кпл ufc octagon alash pride naiza футбол главная группа реал боруссия новости трибуна матчи фэнтези рпл лч апл ла лига серия бундеслига турниры евро рпл лига чемпионов паулиста ла лига лига европы лига конференций апл бундеслига серия китайская суперлига лига кубок россии первая лига вторая лига вторая лига б казахстанская лига эредивизи примейра лига саудовская пролига млс команды реал мадрид барселона манчестер сити ливерпуль зенит спартак сборная россии краснодар байер бавария мю челси арсенал боруссия д динамо м интер майами игроки месси роналду беллингем мбаппе холанд кейн в

In [108]:
print(data[0])

{'id': 1, 'url': 'https://www.sports.ru/football/1116109365-karlo-anchelotti-vinisius-stradaet-ot-oskorblenij-no-ostaetsya-sosredo.html', 'content': 'карло анчелотти высоко отозвался винисиусе футбол главная главная группа реал боруссия махачев порье трибуна ставки спорт казахстана футбол фигурка хоккей баскет теннис бокс авто лыжи наши приложения ставки главная группа новости трибуна букмекеры бонусы букмекеров приложения букмекеров зарубежные букмекеры букмекеры кэшбеком ставки киберспорт легальные букмекеры спорт казахстана главная группа новости трибуна кпл ufc octagon alash pride naiza футбол главная группа реал боруссия новости трибуна матчи фэнтези рпл лч апл ла лига серия бундеслига турниры евро рпл лига чемпионов паулиста ла лига лига европы лига конференций апл бундеслига серия китайская суперлига лига кубок россии первая лига вторая лига вторая лига б казахстанская лига эредивизи примейра лига саудовская пролига млс команды реал мадрид барселона манчестер сити ливерпуль зени

In [109]:
import re
import numpy as np
from collections import defaultdict
from sklearn.feature_extraction.text import TfidfVectorizer

documents = [doc['content'] for doc in data]

In [110]:
# Прямой индекс
def create_forward_index(data):
    forward_index = {}
    for doc in data:
        forward_index[doc['id']] = doc['content']
    return forward_index

forward_index = create_forward_index(data)

# Функция для поиска в прямом индексе
def search_forward_index(query, forward_index):
    query_words = re.findall(r'\w+', query.lower())
    doc_scores = defaultdict(int)
    for doc_id, content in forward_index.items():
        for word in query_words:
            if word in content.lower():
                doc_scores[doc_id] += 1
    sorted_docs = sorted(doc_scores.items(), key=lambda item: item[1], reverse=True)
    return [doc_id for doc_id, _ in sorted_docs]

In [111]:
# Обратный индекс
def create_inverted_index(documents):
    inverted_index = defaultdict(list)
    for doc_id, content in enumerate(documents):
        words = re.findall(r'\w+', content.lower())
        for word in words:
            inverted_index[word].append(doc_id)
    return inverted_index

inverted_index = create_inverted_index(documents)

# Функция для поиска в обратном индексе
def search_inverted_index(query, index):
    query_words = re.findall(r'\w+', query.lower())
    doc_scores = defaultdict(int)
    for word in query_words:
        if word in index:
            for doc_id in index[word]:
                doc_scores[doc_id] += 1
    sorted_docs = sorted(doc_scores.items(), key=lambda item: item[1], reverse=True)
    return [doc_id for doc_id, _ in sorted_docs]

In [112]:
# TF-IDF индекс
vectorizer = TfidfVectorizer()
tfidf_matrix = vectorizer.fit_transform(documents)

# Функция для поиска в TF-IDF индексе
def search_tfidf_index(query, tfidf_matrix, vectorizer):
    query_vec = vectorizer.transform([query])
    cosine_similarities = (tfidf_matrix * query_vec.T).toarray().flatten()
    ranked_results = np.argsort(cosine_similarities)[::-1]
    return ranked_results, cosine_similarities

In [113]:
# Запрос
query = "сосо павлиашвили"

In [114]:
# Прямой
forward_index_results = search_forward_index(query, forward_index)

print("Forward Index Results:")
for doc_id in forward_index_results[:5]:
    print(f"Document ID: {doc_id}, URL: {data[doc_id-1]['url']}")

# Обратный
inverted_index_results = search_inverted_index(query, inverted_index)

print("Inverted Index Results:")
for doc_id in inverted_index_results[:5]:
    print(f"Document ID: {data[doc_id]['id']}, URL: {data[doc_id]['url']}")

# TF-IDF
tfidf_index_results, similarities = search_tfidf_index(query, tfidf_matrix, vectorizer)

print("TF-IDF Index Results:")
for idx in tfidf_index_results[:5]:
    print(f"Document ID: {data[idx]['id']}, URL: {data[idx]['url']}, Similarity: {similarities[idx]:.4f}")

Forward Index Results:
Document ID: 7, URL: https://www.sports.ru/football/1116109328-xvicha-dal-pszh-soglasie-na-podpisanie-dolgosrochnogo-kontrakta-parizh.html
Document ID: 75, URL: https://www.sports.ru/football/1116108614-soso-pavliashvili-o-xviche.html
Document ID: 101, URL: https://www.sports.ru/football/1116109328-xvicha-dal-pszh-soglasie-na-podpisanie-dolgosrochnogo-kontrakta-parizh.html
Inverted Index Results:
Document ID: 75, URL: https://www.sports.ru/football/1116108614-soso-pavliashvili-o-xviche.html
Document ID: 7, URL: https://www.sports.ru/football/1116109328-xvicha-dal-pszh-soglasie-na-podpisanie-dolgosrochnogo-kontrakta-parizh.html
Document ID: 101, URL: https://www.sports.ru/football/1116109328-xvicha-dal-pszh-soglasie-na-podpisanie-dolgosrochnogo-kontrakta-parizh.html
TF-IDF Index Results:
Document ID: 75, URL: https://www.sports.ru/football/1116108614-soso-pavliashvili-o-xviche.html, Similarity: 0.3815
Document ID: 7, URL: https://www.sports.ru/football/1116109328-